### Installing Packages

In [1]:
import numpy as np
import pandas as pd
import math
import matplotlib.pyplot as plt

#### Create Fictional Data

In [2]:
Movie_Ratings = {'Rating_1' : [0,0,1,1,1],
                 'Rating_2' : [1,1,0,0,1],
                 'My_Ratings' : [0,0,1,1,1]}

movie_df = pd.DataFrame(Movie_Ratings)
initial_weights = [0.5,0.5]
initail_intercept = 3.0

In [3]:
x_test = pd.DataFrame({'Rating_1' : [0,0,1,1,1],
                 'Rating_2' : [1,1,0,0,1]})
y_test = pd.DataFrame({'My_Ratings' : [0,0,1,1,1]})
initial_weights = [0.5,0.5]
initail_intercept = 3.0

##### Creating a Function to calculate z-values

In [4]:
def get_z_vals(x, weights_vector, intercept):
    z = []
    for i in range(len(x)):
        line = []
        for j in range(x.shape[1]):
            line.append(x.iloc[i,:][j] * weights_vector[j])
        z.append(sum(line) + intercept)
    return z

In [5]:
def get_z_vals(x, weights_vector, intercept):
    return np.dot(x, weights_vector) + intercept

In [6]:
get_z_vals(x_test, initial_weights, initail_intercept)

array([3.5, 3.5, 3.5, 3.5, 4. ])

##### $y_{pred}$ function

In [143]:
def get_y_hat(z_vector):
    y_hat = []
    for z_score in z_vector:
        y_hat.append(1 / (1 + math.exp(-z_score)))
    
    return np.array(y_hat)

In [145]:
def get_y_hat(z):
    return 1 / (1+ np.exp(-z))

In [146]:
get_y_hat(get_z_vals(x_test, initial_weights, initail_intercept))

array([0.97068777, 0.97068777, 0.97068777, 0.97068777, 0.98201379])

#### Cost function

In [10]:
def cost_fun(y, y_hat):
    print(y_hat[i])
    return -1/len(y_hat) * sum([y.iloc[i]*math.log(y_hat[i]) + 
                     (1-y.iloc[i])* math.log(1-(y_hat[i]))for i in range(len(y_hat))])[0]

In [44]:
def cost_fun(y, y_hat):
    return (-1/len(y_hat)) * np.sum(np.array(y) * np.log(y_hat) + (1-np.array(y)) * (np.log(1 - y_hat)))

In [156]:
cost_fun(y_test, get_y_hat(get_z_vals(x_test, initial_weights, initail_intercept)))

In [157]:
def cost_fun(y, y_hat):
    return log_loss(y, y_hat)

##### Updating Parameters

In [13]:
def update_intercept(y, y_hat, alpha, intercept):
    
    difference = [y_hat[i] - y.iloc[i] for i in range(len(y_hat))]
    
    return (intercept - (alpha * (sum(difference)/len(difference))))[0]

In [14]:
update_intercept(y_test, get_y_hat(get_z_vals(x_test, initial_weights, initail_intercept)), 0.01, initail_intercept)

2.996270470265935

In [134]:
def update_weight_vector(y, y_hat, alpha, weight_vec, x):
    
    difference = [y_hat[i] - y.iloc[i] for i in range(len(y_hat))]
    
    del_w = []
    for i in range(len(weight_vec)):
        delta_w = sum([difference[j] * x.iloc[j][i] for j in range(len(difference))]) / len(difference)
        del_w.append(delta_w)
    print(del_w)
    return [(weight_vec[i] - (alpha) * del_w[i])[0] for i in range(len(weight_vec))]


In [142]:
def update_weight_vector(y, y_hat, alpha, weight_vec, x):
    
    diff = np.subtract(y_hat ,np.array(y).reshape(1,len(y)))
    return np.subtract(weight_vec, (alpha * np.dot(diff, x)))[0]

In [141]:
np_update_weight_vector(y_test, get_y_hat(get_z_vals(x_test, initial_weights, initail_intercept)),
                     0.01, initial_weights, x_test)

array([0.50076611, 0.48076611])

In [137]:
update_weight_vector(y_test, get_y_hat(get_z_vals(x_test, initial_weights, initail_intercept)),
                     0.01, initial_weights, x_test)

[My_Ratings   -0.015322
dtype: float64, My_Ratings    0.384678
dtype: float64]


[0.5001532213429296, 0.4961532213429296]

### Testing

In [22]:
def gradient_descent(x,y, init_w, init_b, alpha = 0.01):
    
    #Get z values using x, init_w and init b
    z = get_z_vals(x, init_w, init_b)
        
    #Get y prediction values
    y_hat = get_y_hat(z)
        
    # Calc Cost Function 
    Cost_Fun = cost_fun(y, y_hat)
    
    #Delta w and Delta b
    intercept_new = update_intercept(y, y_hat, alpha, init_b)
        
    new_weights = update_weight_vector(y, y_hat, alpha, init_w, x)

    
    return new_weights, Cost_Fun, intercept_new, y_hat

In [23]:
gradient_descent(x_test,y_test, initial_weights, initail_intercept)

[0.97068777 0.97068777 0.97068777 0.97068777 0.98201379]


(array([0.50076611, 0.48076611]),
 7.337151601008292,
 2.996270470265935,
 array([0.97068777, 0.97068777, 0.97068777, 0.97068777, 0.98201379]))

##### Creting Iterative Function to handle iterations/tolerance

In [152]:
def grad_its(x,y, init_w, init_b, alpha = 0.01, tol = 1e-8, max_its = 1000):
    i = 0
    new_weights, Cost_Fun, intercept_new, y_hat = gradient_descent(x,y, init_w, init_b, alpha)
    #set_trace()
    new_weights, Cost_Fun_new, intercept_new , y_hat = gradient_descent(x,y,new_weights, intercept_new, alpha)
    
    while (abs(Cost_Fun - Cost_Fun_new) > tol) and i < max_its:
        Cost_Fun = Cost_Fun_new
        new_weights, Cost_Fun_new, intercept_new, y_hat = gradient_descent(x,y,new_weights, intercept_new, alpha)
        i += 1 
        if i / max_its == 0.25:
            print("Quarter of the way there!")
        elif i / max_its == 0.5:
            print("Halfway there!")
        elif i / max_its == 0.75:
            print("One more quarter to go!")
    
    return new_weights, Cost_Fun_new, intercept_new, y_hat

In [155]:
grad_its(x_test,y_test, [1.6533184539468795, -1.9471455873302386], 1.0005869287065845,alpha = 0.1, max_its = 1000)

TypeError: unsupported operand type(s) for -: 'NoneType' and 'NoneType'

In [27]:
blobs = pd.read_csv("/Users/joshocurry/Downloads/blobs300.csv")
blobs

X1        X2        X3        X4  Class
0    0.726739  0.035393  1.759229  1.633698      1
1    2.691834  2.715685 -0.085346  2.131453      0
2    2.446502  3.853792  0.487143  2.138328      0
3    0.899178 -0.596257  1.764085  1.863523      1
4    0.520531  0.521058  1.607952  1.757980      1
..        ...       ...       ...       ...    ...
295  1.324187  0.125884  1.759156  2.089274      1
296  2.095409  3.344137  0.725646  2.181084      0
297  1.524761  3.281810 -0.855361  2.572439      0
298  2.597079  3.353805  1.101402  1.850293      0
299  2.753740  3.249708 -0.741540  2.037166      0

[300 rows x 5 columns]

In [28]:
x_blobs = blobs[['X1', 'X2', 'X3', 'X4']]
y_blobs = blobs[['Class']]

In [29]:
grad_its(x_blobs,y_blobs, [1,1,1,1] , 10)

[0.99999929 0.99999997 0.99999999 0.99999911 0.99999945 0.99999995
 0.99999999 0.99999999 0.99999997 0.99999972 0.99999969 0.99999993
 0.99999749 0.99999997 0.99999996 0.99999862 0.99999899 0.99999975
 0.99999971 0.99999835 0.99999999 0.99999964 0.99999998 0.99999999
 0.99999995 0.99999993 1.         0.99999999 0.99999402 0.99999999
 0.99999999 0.99999997 0.99999991 0.99999709 0.99999996 0.99999993
 0.99999999 0.99999996 0.99999881 0.9999999  0.99999909 0.99999999
 0.99999826 0.99999717 0.99999798 0.99999886 0.99999993 0.99999998
 0.99999992 0.99999776 0.99999999 0.99999829 0.99999927 0.99999987
 0.99999976 0.9999989  0.99999999 0.9999987  0.99999999 0.99999996
 0.99999958 0.99999294 0.99999998 0.99999937 0.99999997 0.99999997
 0.99999999 0.99999983 0.99999734 0.99999992 0.99998342 0.99999999
 0.99999988 0.99999993 0.99999945 0.99999662 0.99999998 0.9999991
 0.99999951 0.99999843 0.99999787 1.         0.99999941 1.
 0.99999879 0.99999998 0.99999997 0.99999645 0.99999993 0.9999999
 1.  

[9.99881959e-01 2.65707320e-04 7.28438682e-06 9.99985373e-01
 9.99210494e-01 2.20758992e-05 1.63257723e-04 4.57133826e-05
 6.49160865e-04 9.99333661e-01 9.95538797e-01 1.38521132e-04
 9.99679170e-01 2.07030856e-05 1.11428980e-04 9.97803938e-01
 9.99934896e-01 9.93149606e-01 2.25265949e-02 9.99673001e-01
 1.16039231e-05 9.92206505e-01 4.82764224e-07 5.75236257e-06
 1.40095589e-05 1.05631396e-04 1.56610816e-07 2.73456269e-05
 9.99832735e-01 1.66451068e-04 6.43665818e-05 3.86795879e-05
 8.06319577e-05 9.99395903e-01 3.99919728e-03 2.23788014e-05
 2.39258594e-04 3.27807527e-04 9.98649483e-01 1.69549251e-05
 9.99475291e-01 1.19853469e-06 9.99432638e-01 9.99896087e-01
 9.87613315e-01 9.99554827e-01 8.28738121e-05 3.87255146e-05
 6.40032365e-04 9.94738358e-01 5.11158043e-06 9.99882815e-01
 9.99953787e-01 4.54332294e-04 1.36822012e-02 9.89253436e-01
 6.27755890e-05 9.94009664e-01 2.79759882e-06 2.42942259e-05
 9.53553091e-01 9.92588948e-01 8.19803549e-05 9.97822890e-01
 2.74005446e-04 7.832935

[9.99937843e-01 9.97340823e-04 3.34546787e-05 9.99992106e-01
 9.99609780e-01 7.49113815e-05 6.24172262e-04 1.78521623e-04
 2.21045970e-03 9.99700327e-01 9.98161940e-01 4.24463519e-04
 9.99805115e-01 7.55896224e-05 4.22083900e-04 9.98822401e-01
 9.99967517e-01 9.96964456e-01 5.16817827e-02 9.99814246e-01
 4.58416839e-05 9.96376330e-01 1.80949488e-06 2.36559982e-05
 4.14087383e-05 3.28379824e-04 8.21971147e-07 1.28527911e-04
 9.99892214e-01 6.45568632e-04 2.54121340e-04 1.29037318e-04
 2.65170454e-04 9.99629285e-01 1.31181899e-02 6.92109839e-05
 1.07355451e-03 1.11443086e-03 9.99272589e-01 4.52591666e-05
 9.99735839e-01 5.62551678e-06 9.99677562e-01 9.99938976e-01
 9.92941484e-01 9.99770636e-01 2.72604463e-04 1.46533809e-04
 1.83669374e-03 9.96969552e-01 2.10774837e-05 9.99936037e-01
 9.99974495e-01 1.31367225e-03 3.41738889e-02 9.94461267e-01
 2.42622239e-04 9.97098848e-01 1.15014091e-05 8.74012577e-05
 9.76579627e-01 9.94955523e-01 3.09138726e-04 9.99094938e-01
 9.42521944e-04 2.789401

[9.99954979e-01 1.82718433e-03 6.70675172e-05 9.99994254e-01
 9.99724687e-01 1.29370368e-04 1.15118498e-03 3.31159246e-04
 3.86065217e-03 9.99798245e-01 9.98813189e-01 6.97938583e-04
 9.99847816e-01 1.35376490e-04 7.76614585e-04 9.99129715e-01
 9.99977263e-01 9.97957615e-01 7.43747626e-02 9.99859854e-01
 8.53840701e-05 9.97499012e-01 3.23986041e-06 4.48460889e-05
 6.63333447e-05 5.45753969e-04 1.74126108e-06 2.62058164e-04
 9.99913654e-01 1.20209584e-03 4.75112654e-04 2.21236641e-04
 4.53592584e-04 9.99708556e-01 2.25552458e-02 1.14038784e-04
 2.15549116e-03 1.94451146e-03 9.99462659e-01 6.88757406e-05
 9.99812284e-01 1.13280870e-05 9.99756690e-01 9.99953503e-01
 9.94608169e-01 9.99835080e-01 4.66450525e-04 2.68237513e-04
 2.94188569e-03 9.97676273e-01 3.98220052e-05 9.99952899e-01
 9.99981129e-01 2.11440663e-03 5.12673242e-02 9.95973308e-01
 4.48551023e-04 9.97966766e-01 2.16646160e-05 1.55671207e-04
 9.83110016e-01 9.95784958e-01 5.65197404e-04 9.99415117e-01
 1.65218195e-03 4.958261

[9.99964547e-01 2.60988402e-03 1.00495249e-04 9.99995512e-01
 9.99785502e-01 1.74438505e-04 1.64422443e-03 4.71179430e-04
 5.33156877e-03 9.99848023e-01 9.99130240e-01 9.10645204e-04
 9.99872672e-01 1.87355972e-04 1.11245726e-03 9.99292683e-01
 9.99982749e-01 9.98443743e-01 9.08399980e-02 9.99885817e-01
 1.21542626e-04 9.98054349e-01 4.38843062e-06 6.44428673e-05
 8.37412161e-05 7.21595775e-04 2.66828335e-06 4.00991978e-04
 9.99926909e-01 1.73546567e-03 6.82607122e-04 2.97142058e-04
 6.13764493e-04 9.99754324e-01 3.10985061e-02 1.48360543e-04
 3.30435317e-03 2.68251481e-03 9.99565142e-01 8.37077098e-05
 9.99853543e-01 1.68597487e-05 9.99801742e-01 9.99962264e-01
 9.95485845e-01 9.99870195e-01 6.31130253e-04 3.79416133e-04
 3.80532158e-03 9.98055426e-01 5.66408205e-05 9.99962578e-01
 9.99984952e-01 2.75065909e-03 6.42886359e-02 9.96745034e-01
 6.38585588e-04 9.98415844e-01 3.06469732e-05 2.15308106e-04
 9.86279225e-01 9.96230458e-01 8.00110173e-04 9.99574158e-01
 2.28155907e-03 6.879192

...

[9.99999752e-01 1.21938697e-03 3.23025334e-05 9.99999989e-01
 9.99997652e-01 9.66171656e-06 6.30513035e-04 8.42968057e-05
 1.78130032e-03 9.99998864e-01 9.99995388e-01 2.30669828e-05
 9.99994950e-01 1.66491643e-05 5.94127095e-04 9.99940649e-01
 9.99999983e-01 9.99966320e-01 2.68605706e-02 9.99997735e-01
 2.36211814e-05 9.99911399e-01 4.65592591e-08 9.26361544e-06
 5.72008033e-07 6.49287072e-05 2.91362822e-07 4.05965022e-04
 9.99997870e-01 1.54563158e-03 2.21940687e-04 2.15499613e-05
 7.71208152e-05 9.99986895e-01 3.22962549e-02 4.48897106e-06
 1.12792253e-02 8.48752335e-04 9.99982110e-01 2.44169918e-07
 9.99998566e-01 1.93396876e-06 9.99997075e-01 9.99999773e-01
 9.99374176e-01 9.99998199e-01 1.02895783e-04 1.33356656e-04
 3.10496956e-04 9.99761123e-01 2.25382124e-06 9.99999700e-01
 9.99999902e-01 2.88753634e-04 1.37161276e-02 9.99635544e-01
 1.53242563e-04 9.99966110e-01 1.37268458e-06 2.45553943e-05
 9.96533754e-01 9.97701523e-01 1.69972473e-04 9.99998574e-01
 6.38710547e-04 1.301208

[9.99999755e-01 1.21576314e-03 3.22142591e-05 9.99999989e-01
 9.99997674e-01 9.60002163e-06 6.29070725e-04 8.39869126e-05
 1.77643334e-03 9.99998875e-01 9.99995434e-01 2.28600283e-05
 9.99994981e-01 1.65608177e-05 5.92579636e-04 9.99940862e-01
 9.99999983e-01 9.99966591e-01 2.68003411e-02 9.99997753e-01
 2.35544378e-05 9.99911934e-01 4.61347956e-08 9.22530957e-06
 5.66506472e-07 6.46075094e-05 2.89898805e-07 4.05769761e-04
 9.99997884e-01 1.54610910e-03 2.21411508e-04 2.14449716e-05
 7.66902891e-05 9.99986971e-01 3.22863118e-02 4.45854058e-06
 1.13009115e-02 8.46186087e-04 9.99982217e-01 2.41349384e-07
 9.99998578e-01 1.92438569e-06 9.99997102e-01 9.99999776e-01
 9.99376848e-01 9.99998212e-01 1.02488048e-04 1.33224159e-04
 3.08861044e-04 9.99762069e-01 2.23640423e-06 9.99999703e-01
 9.99999903e-01 2.87245923e-04 1.36559250e-02 9.99636837e-01
 1.52763427e-04 9.99966336e-01 1.36495170e-06 2.44295252e-05
 9.96545185e-01 9.97703096e-01 1.69238828e-04 9.99998588e-01
 6.36851177e-04 1.296295

[9.99999757e-01 1.21216038e-03 3.21266671e-05 9.99999989e-01
 9.99997696e-01 9.53900791e-06 6.27639145e-04 8.36797958e-05
 1.77160226e-03 9.99998885e-01 9.99995479e-01 2.26557615e-05
 9.99995012e-01 1.64733656e-05 5.91040406e-04 9.99941072e-01
 9.99999983e-01 9.99966859e-01 2.67406244e-02 9.99997770e-01
 2.34883366e-05 9.99912463e-01 4.57163604e-08 9.18735997e-06
 5.61086849e-07 6.42895526e-05 2.88449158e-07 4.05575587e-04
 9.99997897e-01 1.54659372e-03 2.20886628e-04 2.13411047e-05
 7.62637597e-05 9.99987047e-01 3.22764240e-02 4.42847935e-06
 1.13225299e-02 8.43638491e-04 9.99982323e-01 2.38575646e-07
 9.99998591e-01 1.91489546e-06 9.99997128e-01 9.99999778e-01
 9.99379498e-01 9.99998226e-01 1.02083932e-04 1.33093680e-04
 3.07241914e-04 9.99763005e-01 2.21919566e-06 9.99999706e-01
 9.99999904e-01 2.85752765e-04 1.35961999e-02 9.99638118e-01
 1.52288310e-04 9.99966560e-01 1.35730887e-06 2.43048573e-05
 9.96556540e-01 9.97704658e-01 1.68511137e-04 9.99998601e-01
 6.35006507e-04 1.291424

[9.99999759e-01 1.21000875e-03 3.20744359e-05 9.99999989e-01
 9.99997709e-01 9.50272227e-06 6.26785293e-04 8.34968428e-05
 1.76872066e-03 9.99998892e-01 9.99995506e-01 2.25344724e-05
 9.99995031e-01 1.64213184e-05 5.90120788e-04 9.99941197e-01
 9.99999983e-01 9.99967019e-01 2.67050377e-02 9.99997780e-01
 2.34489805e-05 9.99912778e-01 4.54681456e-08 9.16475918e-06
 5.57873735e-07 6.41003145e-05 2.87586182e-07 4.05459598e-04
 9.99997905e-01 1.54688786e-03 2.20573742e-04 2.12793165e-05
 7.60097386e-05 9.99987091e-01 3.22705175e-02 4.41061728e-06
 1.13354685e-02 8.42118797e-04 9.99982386e-01 2.36933450e-07
 9.99998598e-01 1.90924532e-06 9.99997144e-01 9.99999779e-01
 9.99381077e-01 9.99998234e-01 1.01843181e-04 1.33016350e-04
 3.06278388e-04 9.99763564e-01 2.20896915e-06 9.99999707e-01
 9.99999905e-01 2.84863771e-04 1.35605916e-02 9.99638880e-01
 1.52005148e-04 9.99966693e-01 1.35276578e-06 2.42306261e-05
 9.96563316e-01 9.97705589e-01 1.68077350e-04 9.99998609e-01
 6.33906684e-04 1.288522

(array([-2.10486482, -5.02127072,  2.72114134,  1.32037664]),
 1625.5293953769647,
 10.003543415091794,
 array([9.99999759e-01, 1.21000875e-03, 3.20744359e-05, 9.99999989e-01,
        9.99997709e-01, 9.50272227e-06, 6.26785293e-04, 8.34968428e-05,
        1.76872066e-03, 9.99998892e-01, 9.99995506e-01, 2.25344724e-05,
        9.99995031e-01, 1.64213184e-05, 5.90120788e-04, 9.99941197e-01,
        9.99999983e-01, 9.99967019e-01, 2.67050377e-02, 9.99997780e-01,
        2.34489805e-05, 9.99912778e-01, 4.54681456e-08, 9.16475918e-06,
        5.57873735e-07, 6.41003145e-05, 2.87586182e-07, 4.05459598e-04,
        9.99997905e-01, 1.54688786e-03, 2.20573742e-04, 2.12793165e-05,
        7.60097386e-05, 9.99987091e-01, 3.22705175e-02, 4.41061728e-06,
        1.13354685e-02, 8.42118797e-04, 9.99982386e-01, 2.36933450e-07,
        9.99998598e-01, 1.90924532e-06, 9.99997144e-01, 9.99999779e-01,
        9.99381077e-01, 9.99998234e-01, 1.01843181e-04, 1.33016350e-04,
        3.06278388e-04, 9.997635

In [31]:
blob_opt = [-1.2974544127210041,
  -2.8621849481304396,
  0.9455682174016076,
  -0.6800520240761868]
b_opt = 8.901394350229799

z = []
for i in range(len(x_blobs)):
    line = []
    for j in range(x_blobs.shape[1]):
        line.append(x_blobs.iloc[i,:][j] * blob_opt[j])
    z.append(sum(line) + b_opt)

#Get y prediction values
y_hat = []
for z_score in z:
    y_hat.append(1/(1+math.exp(-z_score)))
       
errors = []
for pair in list(zip(y_blobs['Class'],y_hat)):
    errors.append(abs(pair[0] - pair[1]))
    
print(sum(errors)/len(errors))
print(max(errors))

0.015672735914413042
0.3633951503524396


In [32]:
get_z_vals(x_blobs, blob_opt, b_opt)

array([  8.40965499,  -3.89412933,  -6.29664233,   9.84211967,
         7.05957396,  -5.61983861,  -4.08112601,  -4.94685375,
        -3.14405586,   7.18937807,   5.7172666 ,  -4.33332834,
         7.57673279,  -5.61269969,  -4.58071321,   6.15616065,
         8.69922672,   5.57985836,  -0.67253339,   7.58567216,
        -5.94248782,   5.43458199,  -8.23247445,  -6.50381978,
        -5.76496425,  -4.49242247,  -9.04882736,  -5.36855002,
         7.89531845,  -4.03379168,  -4.72530894,  -5.09634684,
        -4.85517546,   7.11839521,  -1.86563014,  -5.54517916,
        -3.86954697,  -3.71198979,   6.58050769,  -5.67551491,
         7.22795772,  -7.59117641,   7.22530308,   8.32921728,
         4.98794754,   7.29617189,  -4.71526317,  -5.03089553,
        -3.16745729,   5.565661  ,  -6.5640498 ,   8.22022539,
         9.12995478,  -3.52915089,  -1.14072179,   5.05609332,
        -4.7529481 ,   5.3639983 ,  -6.80704973,  -5.5836785 ,
         4.21410266,   5.26219901,  -4.68925879,   6.03

In [33]:
pairs = list(zip(y_blobs['Class'],[round(val) for val in y_hat]))

print(sum([1 for pair in pairs if pair[0] == pair[1]])/len(pairs))

1.0


In [34]:
circles = pd.read_csv("/Users/joshocurry/Downloads/circles600.csv")
circles

X1        X2  Class
0   -0.371514  0.012406      1
1   -1.014230  0.223095      0
2   -1.123804  0.249026      0
3    0.213708  0.032912      1
4   -0.833531 -0.491312      0
..        ...       ...    ...
595 -0.100827 -0.386171      1
596  0.533986 -0.144301      1
597 -0.445042 -0.042955      1
598 -0.052254 -0.324085      1
599 -0.857302 -0.365210      0

[600 rows x 3 columns]

In [35]:
x_circles = circles[['X1', 'X2']]
y_circles = circles[['Class']]

In [37]:
grad_its(x_circles,y_circles, [0.1,0.1] , 0.05, max_its=500, alpha = 0.1, tol = 1e-8)

[0.50352226 0.49272213 0.49063163 0.51865684 0.47939059 0.49273
 0.51952866 0.4909539  0.50766444 0.51916174 0.50571589 0.5384849
 0.50636273 0.54344019 0.51228382 0.52448895 0.48069629 0.52104172
 0.54354394 0.50274017 0.50926417 0.50569219 0.52048794 0.50991235
 0.51917918 0.47291112 0.51584795 0.49847012 0.50889192 0.4848938
 0.47466243 0.49927354 0.49099718 0.47818834 0.48484941 0.53139178
 0.47937905 0.4895256  0.52925583 0.52261046 0.47832807 0.48566133
 0.48932067 0.50918928 0.52008071 0.54422718 0.5150418  0.51085826
 0.50370644 0.50195461 0.50513759 0.5304112  0.53831805 0.53926012
 0.54621459 0.47682463 0.50808254 0.5001325  0.54675847 0.4851722
 0.54479828 0.54990581 0.50277054 0.50359497 0.51821568 0.47951332
 0.51619254 0.51493003 0.51686686 0.48435546 0.49784552 0.48241996
 0.53312204 0.5115752  0.51495164 0.5022397  0.51085523 0.49066677
 0.52510739 0.54383738 0.51677529 0.50741872 0.53849307 0.47792084
 0.5210954  0.51128956 0.48521607 0.51237239 0.48650834 0.50135629
 

[0.45241113 0.38145636 0.36828813 0.55233776 0.30640303 0.38209598
 0.55924155 0.37057475 0.47458771 0.55536022 0.4674195  0.67103595
 0.47349416 0.69929295 0.50944659 0.58835244 0.31687041 0.56707144
 0.70110604 0.45407238 0.49214457 0.46912636 0.56176336 0.49587243
 0.55720816 0.27449164 0.53291634 0.41809926 0.48702099 0.34184281
 0.28143485 0.43010372 0.37205453 0.2995976  0.34155261 0.62753871
 0.3093934  0.36656942 0.61507895 0.57549913 0.30131375 0.34007204
 0.36102739 0.49237433 0.56130757 0.70743539 0.52674181 0.5027675
 0.45529135 0.4443051  0.46658743 0.62890672 0.67045895 0.68048977
 0.71865401 0.29263388 0.48737268 0.43230079 0.7178572  0.34364174
 0.71088225 0.73588808 0.44398688 0.458809   0.55347466 0.31153811
 0.53646788 0.5264139  0.53817257 0.33769585 0.42233165 0.32283133
 0.64545549 0.50058179 0.52684933 0.44494094 0.49950703 0.37741972
 0.58795934 0.70167295 0.53448598 0.47881797 0.66985716 0.29937082
 0.5665439  0.5048844  0.3376938  0.50989111 0.34615443 0.44492

[0.76646769 0.92564078 0.94174591 0.32091203 0.98764449 0.92688689
 0.30490073 0.93999779 0.62254121 0.30508165 0.71618107 0.02983294
 0.71066246 0.01585116 0.51020124 0.17411651 0.98691152 0.25313013
 0.01635472 0.81751222 0.6249323  0.72834094 0.25652838 0.60112678
 0.31617831 0.99524354 0.39680481 0.85693689 0.61687208 0.97809408
 0.99348453 0.87009448 0.94191004 0.98936431 0.97819701 0.06989941
 0.98893739 0.95660925 0.09241657 0.20772838 0.98953537 0.97020884
 0.95151889 0.63238642 0.28029652 0.0164423  0.4153684  0.57650255
 0.77149736 0.81098278 0.74871655 0.09827506 0.0308802  0.03202912
 0.01294286 0.99124308 0.6804339  0.84366062 0.01049266 0.97741997
 0.01546318 0.00738043 0.76418188 0.79622639 0.36178976 0.98928711
 0.39570644 0.42193856 0.35557878 0.97886306 0.89388318 0.98131222
 0.07118192 0.50078381 0.42346808 0.79925257 0.55207602 0.95571538
 0.14492996 0.0151568  0.33664406 0.67093487 0.02859127 0.99017992
 0.24668573 0.5573531  0.97206306 0.50627384 0.96800738 0.8421

[0.74826016 0.90197984 0.92040967 0.33144117 0.98597698 0.90688398
 0.33329469 0.91977253 0.531516   0.31255474 0.70754606 0.02628809
 0.72594896 0.01439168 0.49370761 0.1721408  0.98816535 0.25651153
 0.0162439  0.8598505  0.6413104  0.74246887 0.23909363 0.61117908
 0.34789436 0.99556519 0.38785617 0.82522023 0.5938068  0.98146272
 0.99283544 0.89088886 0.9278327  0.98772504 0.98151076 0.05599896
 0.98989867 0.95622673 0.07704406 0.19521987 0.98872758 0.96185897
 0.93591339 0.65855441 0.28843412 0.01974674 0.39182123 0.59830674
 0.77259471 0.81402822 0.77347093 0.12215198 0.0279253  0.03971152
 0.01628462 0.99018058 0.73151961 0.84293957 0.01003263 0.98111415
 0.01909402 0.0080585  0.70096448 0.83632548 0.43202194 0.99114518
 0.40645889 0.40409109 0.32902611 0.98084394 0.91743513 0.97808581
 0.09067014 0.41920196 0.41000723 0.79050256 0.52495449 0.96520238
 0.11305855 0.01396972 0.27138603 0.66739145 0.02317997 0.98962866
 0.23995584 0.56933264 0.96469062 0.4878143  0.96201882 0.8776

[0.27062175 0.12930843 0.10820516 0.69435333 0.00930248 0.11368674
 0.65467243 0.10470904 0.67128639 0.72099262 0.29608052 0.99030051
 0.22862654 0.99496207 0.56380334 0.87807043 0.00474173 0.78766452
 0.99298208 0.06288727 0.32271503 0.21248241 0.83906384 0.37039167
 0.63120165 0.00157877 0.66977701 0.22245219 0.46045636 0.007035
 0.0039228  0.05739449 0.07966566 0.0082197  0.0070445  0.98046454
 0.00401023 0.02838044 0.9687559  0.87262309 0.00643853 0.03939861
 0.07826156 0.28466316 0.74549268 0.98684908 0.69253886 0.3622135
 0.20312251 0.15517288 0.1622998  0.87166505 0.98898943 0.96749003
 0.98849874 0.00593884 0.16763427 0.13206107 0.99634552 0.00701838
 0.98661932 0.99628958 0.43857399 0.08393813 0.45184632 0.00278858
 0.60955745 0.66852227 0.76422635 0.0084445  0.03470303 0.01694758
 0.90640279 0.76051032 0.65359619 0.2030809  0.54934683 0.01271091
 0.95739122 0.99498227 0.86942594 0.33205071 0.99299638 0.00559774
 0.82170985 0.415899   0.03498765 0.57461667 0.03357254 0.0547346

...

[0.32577537 0.05393517 0.03983243 0.55748428 0.68647653 0.09153404
 0.80015187 0.05358633 0.0058668  0.4998259  0.48508378 0.01787103
 0.83623033 0.01920525 0.28049417 0.23994231 0.98350081 0.39963711
 0.06966966 0.99576179 0.78955254 0.83764927 0.11801423 0.70043789
 0.83174754 0.98589989 0.30834042 0.08498323 0.24567772 0.99153214
 0.8387147  0.98227234 0.15608859 0.65319084 0.99128883 0.00663629
 0.98278316 0.84952525 0.01371003 0.12470123 0.83967114 0.16680381
 0.07631184 0.87845096 0.49973404 0.55392546 0.16301669 0.81488582
 0.69375689 0.76176986 0.93260626 0.89944203 0.02658676 0.76115795
 0.6780564  0.76469548 0.98243645 0.71753102 0.0316468  0.99274249
 0.64255096 0.15520017 0.01808554 0.99104438 0.98035808 0.99601626
 0.59458174 0.21954309 0.11093923 0.97746891 0.99502319 0.50803019
 0.90476156 0.00830864 0.26895384 0.51218701 0.18750118 0.99589262
 0.00539139 0.02323328 0.00734224 0.54726779 0.00512197 0.87918692
 0.22860177 0.69764911 0.20316681 0.2562338  0.3722049  0.9950

[0.32577495 0.05393507 0.03983235 0.55748384 0.68647609 0.09153388
 0.80015159 0.05358622 0.00586679 0.49982545 0.4850833  0.017871
 0.83623007 0.01920521 0.2804938  0.23994198 0.98350077 0.39963668
 0.06966955 0.99576179 0.78955223 0.83764901 0.11801404 0.7004375
 0.8317473  0.98589987 0.30834003 0.08498308 0.24567737 0.99153212
 0.83871442 0.98227231 0.15608832 0.65319037 0.99128881 0.00663628
 0.98278312 0.849525   0.01371    0.12470103 0.83967086 0.16680353
 0.0763117  0.87845077 0.49973359 0.55392506 0.16301644 0.81488554
 0.69375649 0.76176951 0.93260615 0.89944188 0.02658671 0.76115765
 0.67805605 0.76469511 0.98243642 0.71753063 0.03164674 0.99274248
 0.64255059 0.15519996 0.01808551 0.99104436 0.98035805 0.99601626
 0.5945813  0.21954277 0.11093905 0.97746887 0.99502318 0.50802968
 0.90476142 0.00830862 0.26895348 0.51218653 0.18750089 0.99589261
 0.00539138 0.02323324 0.00734222 0.54726732 0.00512196 0.87918671
 0.22860145 0.69764872 0.20316648 0.25623345 0.37220442 0.9950430

[0.32577454 0.05393497 0.03983227 0.5574834  0.68647566 0.09153371
 0.80015131 0.05358612 0.00586677 0.49982501 0.48508284 0.01787097
 0.83622982 0.01920518 0.28049343 0.23994167 0.98350074 0.39963626
 0.06966944 0.99576178 0.78955193 0.83764876 0.11801385 0.70043712
 0.83174705 0.98589984 0.30833965 0.08498293 0.24567703 0.99153211
 0.83871415 0.98227228 0.15608807 0.65318991 0.99128879 0.00663627
 0.98278309 0.84952475 0.01370998 0.12470084 0.83967059 0.16680325
 0.07631156 0.87845057 0.49973315 0.55392466 0.16301619 0.81488527
 0.69375609 0.76176917 0.93260603 0.89944173 0.02658667 0.76115735
 0.67805571 0.76469475 0.98243639 0.71753025 0.03164669 0.99274246
 0.64255023 0.15519975 0.01808548 0.99104435 0.98035801 0.99601625
 0.59458088 0.21954246 0.11093887 0.97746882 0.99502317 0.50802918
 0.90476128 0.00830861 0.26895313 0.51218606 0.18750061 0.9958926
 0.00539137 0.02323321 0.00734221 0.54726687 0.00512195 0.8791865
 0.22860114 0.69764834 0.20316616 0.2562331  0.37220396 0.995043

[0.32577414 0.05393487 0.0398322  0.55748298 0.68647524 0.09153355
 0.80015104 0.05358603 0.00586676 0.49982458 0.4850824  0.01787094
 0.83622958 0.01920515 0.28049307 0.23994136 0.98350071 0.39963585
 0.06966934 0.99576177 0.78955164 0.83764852 0.11801367 0.70043675
 0.83174682 0.98589981 0.30833928 0.08498278 0.2456767  0.99153209
 0.83871389 0.98227225 0.15608781 0.65318947 0.99128878 0.00663626
 0.98278306 0.84952452 0.01370996 0.12470066 0.83967033 0.16680298
 0.07631142 0.87845039 0.49973273 0.55392428 0.16301595 0.81488501
 0.69375571 0.76176885 0.93260592 0.89944158 0.02658662 0.76115707
 0.67805537 0.7646944  0.98243636 0.71752988 0.03164665 0.99274245
 0.64254987 0.15519955 0.01808544 0.99104433 0.98035798 0.99601624
 0.59458046 0.21954216 0.1109387  0.97746878 0.99502316 0.5080287
 0.90476114 0.00830859 0.26895278 0.51218561 0.18750034 0.9958926
 0.00539136 0.02323317 0.0073422  0.54726643 0.00512195 0.87918629
 0.22860084 0.69764797 0.20316585 0.25623276 0.37220352 0.995043

(array([-1.78344888,  5.13153762]),
 760.3813592948692,
 -0.0009702125723146003,
 array([0.32577375, 0.05393478, 0.03983213, 0.55748257, 0.68647483,
        0.0915334 , 0.80015078, 0.05358593, 0.00586675, 0.49982416,
        0.48508196, 0.01787091, 0.83622935, 0.01920512, 0.28049273,
        0.23994106, 0.98350068, 0.39963545, 0.06966924, 0.99576176,
        0.78955135, 0.83764829, 0.1180135 , 0.70043639, 0.83174659,
        0.98589978, 0.30833892, 0.08498264, 0.24567637, 0.99153208,
        0.83871363, 0.98227222, 0.15608757, 0.65318904, 0.99128876,
        0.00663625, 0.98278303, 0.84952428, 0.01370994, 0.12470047,
        0.83967008, 0.16680272, 0.07631129, 0.87845021, 0.49973231,
        0.5539239 , 0.16301572, 0.81488475, 0.69375534, 0.76176853,
        0.93260581, 0.89944144, 0.02658658, 0.76115679, 0.67805504,
        0.76469405, 0.98243633, 0.71752953, 0.0316466 , 0.99274244,
        0.64254952, 0.15519935, 0.01808541, 0.99104432, 0.98035795,
        0.99601623, 0.59458006, 0.2

In [38]:
circles_pred = get_y_hat(get_z_vals(x_circles, [-1.78344888,  5.13153762], -0.0009702125723146003))

In [39]:
pairs = list(zip(y_circles['Class'],[round(val) for val in circles_pred]))

print(sum([1 for pair in pairs if pair[0] == pair[1]])/len(pairs))

0.5116666666666667


In [36]:
np.random.normal(loc = 0, scale = 0.1)

-0.036798101039065015

In [47]:
def one_hidden_layer(x,y,n_hidden_nodes = 4,alpha = 0.01, tol = 1e-8, max_its = 1000):
    
    hidden_dict = dict()
    
    for i in range(n_hidden_nodes):
        
        print(f'Starting Node {i+1} of {n_hidden_nodes} nodes')
        init_w = list(abs(np.random.normal(loc = 0, scale = 0.1, size = (1,x.shape[1])))[0]) 
        
        *_,predictions = grad_its(x,y,
                         init_w,
                         np.random.normal(loc = 0, scale = 0.1)
                         ,alpha, tol, max_its)
        hidden_dict[i] = predictions
        
    hidden_df = pd.DataFrame(hidden_dict)
    
    final_weights = list(abs(np.random.normal(loc = 0, scale = 0.1, size = (1,n_hidden_nodes)))[0]) 
    print('FINAL +++++++++++++++++++++++++++++++++')
    return  grad_its(hidden_df,y,
                         final_weights,
                         np.random.normal(loc = 0, scale = 0.1),
                        alpha, tol, max_its)[-1]
    

In [48]:
blob_pred = one_hidden_layer(x_blobs, y_blobs,alpha = 0.01, tol = 1e-8, max_its = 100)

Starting Node 1 of 4 nodes
Quarter of the way there!
Halfway there!
One more quarter to go!
Starting Node 2 of 4 nodes
Quarter of the way there!
Halfway there!
One more quarter to go!
Starting Node 3 of 4 nodes
Quarter of the way there!
Halfway there!
One more quarter to go!
Starting Node 4 of 4 nodes
Quarter of the way there!
Halfway there!
One more quarter to go!
FINAL +++++++++++++++++++++++++++++++++
Quarter of the way there!
Halfway there!
One more quarter to go!


In [55]:
print([pair for pair in list(zip(np.round(blob_pred), y_blobs.iloc[:,0])) if pair[0] != pair[1]])

[(1.0, 0), (1.0, 0), (1.0, 0), (1.0, 0), (1.0, 0), (1.0, 0), (1.0, 0)]


In [53]:

total = list(zip(blob_pred, y_blobs.iloc[:,0]))
print(sum([1 for pair in total if round(pair[0]) == pair[1]])/len(total))

0.9766666666666667


In [56]:
circles_predictions = one_hidden_layer(x_circles, y_circles, 4, alpha = 0.01, max_its = 1000)

Starting Node 1 of 4 nodes
Quarter of the way there!
Halfway there!
One more quarter to go!
Starting Node 2 of 4 nodes
Quarter of the way there!
Halfway there!
One more quarter to go!
Starting Node 3 of 4 nodes
Quarter of the way there!
Halfway there!
One more quarter to go!
Starting Node 4 of 4 nodes
Quarter of the way there!
Halfway there!
One more quarter to go!
FINAL +++++++++++++++++++++++++++++++++


In [57]:

total = list(zip(circles_predictions, y_circles.iloc[:,0]))
print(sum([1 for pair in total if round(pair[0]) == pair[1]])/len(total))

0.6766666666666666


In [58]:
# This function taken from the CIFAR website

def unpickle(file):
    import pickle
    with open(file, 'rb') as fo:
        dict = pickle.load(fo, encoding='bytes')
    return dict

# Loaded in this way, each of the batch files contains a dictionary with the following elements:
#   data -- a 10000x3072 numpy array of uint8s. Each row of the array stores a 32x32 colour image. 
#           The first 1024 entries contain the red channel values, the next 1024 the green, and the final 1024 the blue. 
#           The image is stored in row-major order, so that the first 32 entries of the array are the red channel values 
#           of the first row of the image.
#   labels -- a list of 10000 numbers in the range 0-9. 
#             The number at index i indicates the label of the ith image in the array data.

In [59]:
def loadbatch(batchname):
    folder = 'cifar-10-batches-py'
    batch = unpickle(folder+"/"+batchname)
    return batch

In [60]:
def loadlabelnames():
    folder = 'cifar-10-batches-py'
    meta = unpickle(folder+"/"+'batches.meta')
    return meta[b'label_names']

In [61]:
batch1 = loadbatch('data_batch_1')
print("Number of items in the batch is", len(batch1))

# Display all keys, so we can see the ones we want
print('All keys in the batch:', batch1.keys())

Number of items in the batch is 4
All keys in the batch: dict_keys([b'batch_label', b'labels', b'data', b'filenames'])


In [62]:
data = batch1[b'data']
labels = batch1[b'labels']
print ("size of data in this batch:", len(data), ", size of labels:", len(labels))
print (type(data))
print(data.shape)

names = loadlabelnames()

size of data in this batch: 10000 , size of labels: 10000
<class 'numpy.ndarray'>
(10000, 3072)


In [63]:
cat_car = []
cc_labels = []
cc_name = []

for i in range(len(data)):
    if labels[i] == 1 or labels[i] == 3:
        cat_car.append(data[i])
        cc_labels.append(labels[i])
        cc_name.append(names[labels[i]])

In [64]:
def gray(pic):
    pic.shape = (3,32,32)
    pic = pic.transpose([1,2,0])

    r, g, b = pic[:,:,0], pic[:,:,1], pic[:,:,2]
    gray = 0.2990 * r + 0.2870 * g + 0.1140 * b
    
    return gray

In [65]:
cat_car_gray = [gray(x) for x in cat_car]

In [66]:
cat_ind = []

for i in cc_labels:
    if i == 1:
        cat_ind.append(0)
    else:
        cat_ind.append(1)
        
cat_ind = pd.DataFrame(cat_ind)
cat_ind

0
0     0
1     0
2     1
3     1
4     1
...  ..
1985  0
1986  0
1987  1
1988  0
1989  0

[1990 rows x 1 columns]

In [67]:
cc_dict = {}

for i in range(len(cat_car_gray)):
    cat_car_gray[i].shape = (1024,)
    cc_dict[i] = cat_car_gray[i]
    
cat_car_df = pd.DataFrame(cc_dict).T

In [162]:
from IPython.core.debugger import set_trace
import warnings
warnings.filterwarnings('ignore')

In [163]:
%%time
pic_pred = grad_its(cat_car_df,cat_ind, list(abs(np.random.normal(loc = 0, scale = 0.1, size = (1,cat_car_df.shape[1])))[0]),
         0.07, alpha = 0.01, tol = 1e-10, max_its = 100)

TypeError: grad_its() got multiple values for argument 'alpha'

In [166]:
%%time
 x = one_hidden_layer(cat_car_df,cat_ind,n_hidden_nodes = 10,alpha = 0.1, tol = 1e-8, max_its = 100)

Starting Node 1 of 10 nodes
Quarter of the way there!
Halfway there!
One more quarter to go!
Starting Node 2 of 10 nodes
Quarter of the way there!
Halfway there!
One more quarter to go!
Starting Node 3 of 10 nodes
Quarter of the way there!
Halfway there!
One more quarter to go!
Starting Node 4 of 10 nodes
Quarter of the way there!
Halfway there!
One more quarter to go!
Starting Node 5 of 10 nodes
Quarter of the way there!
Halfway there!
One more quarter to go!
Starting Node 6 of 10 nodes
Quarter of the way there!
Halfway there!
One more quarter to go!
Starting Node 7 of 10 nodes
Quarter of the way there!
Halfway there!
One more quarter to go!
Starting Node 8 of 10 nodes
Quarter of the way there!
Halfway there!
One more quarter to go!
Starting Node 9 of 10 nodes
Quarter of the way there!
Halfway there!
One more quarter to go!
Starting Node 10 of 10 nodes
Quarter of the way there!
Halfway there!
One more quarter to go!
FINAL +++++++++++++++++++++++++++++++++
Quarter of the way there!
Hal

In [159]:
for i in pic_pred[-1]:
    print(i)

0.0
0.0
0.0
1.0
1.0
0.0
0.0
0.0
1.0
0.0
0.0
0.0
0.0
0.0
0.0
0.0
0.0
0.0
0.0
0.0
0.0
0.0
0.0
0.0
0.0
0.0
0.0
0.0
1.0
0.0
0.0
0.0
0.0
0.0
0.0
0.0
0.0
0.0
0.0
1.0
0.0
0.0
0.0
0.0
0.0
0.0
0.0
0.0
1.0
0.0
1.0
0.0
0.0
0.0
0.0
0.0
1.0
0.0
0.0
0.0
0.0
0.0
0.0
0.0
0.0
1.0
0.0
0.0
0.0
0.0
0.0
0.0
1.0
0.0
0.0
0.0
0.0
0.0
0.0
0.0
0.0
0.0
0.0
0.0
1.0
0.0
0.0
0.0
0.0
0.0
0.0
0.0
1.0
0.0
0.0
0.0
0.0
1.0
0.0
0.0
1.0
0.0
0.0
0.0
0.0
1.0
1.0
0.0
0.0
0.0
0.0
0.0
0.0
0.0
0.0
0.0
0.0
0.0
1.0
0.0
0.0
0.0
0.0
0.0
0.0
0.0
0.0
1.0
0.0
0.0
0.0
0.0
0.0
0.0
0.0
0.0
0.0
0.0
0.0
0.0
0.0
0.0
0.0
0.0
0.0
0.0
1.0
1.0
0.0
0.0
0.0
0.0
0.0
0.0
0.0
0.0
0.0
0.0
0.0
0.0
1.0
0.0
1.0
0.0
0.0
0.0
0.0
0.0
0.0
0.0
0.0
0.0
0.0
0.0
0.0
0.0
1.0
0.0
0.0
0.0
0.0
0.0
0.0
0.0
0.0
0.0
0.0
0.0
0.0
0.0
1.0
0.0
0.0
0.0
0.0
1.0
0.0
0.0
0.0
0.0
0.0
1.0
0.0
0.0
1.0
0.0
0.0
0.0
0.0
0.0
0.0
0.0
0.0
0.0
0.0
0.0
0.0
1.0
0.0
0.0
0.0
1.0
0.0
0.0
0.0
0.0
0.0
1.0
0.0
0.0
0.0
1.0
0.0
0.0
0.0
0.0
1.0
0.0
0.0
0.0
0.0
0.0
0.0
0.0
0.0
0.0
0.0
0.0
0.0
0.0


In [154]:
%%time
gradient_descent(X_scaled,cat_ind, list(abs(np.random.normal(loc = 0, scale = 0.01, size = (1,cat_car_df.shape[1])))[0]),
         0.07, alpha = 0.001)

CPU times: user 1.12 s, sys: 329 ms, total: 1.45 s
Wall time: 360 ms


(array([-0.52326583, -0.52769667, -0.54210482, ..., -0.42492293,
        -0.45108693, -0.43040778]),
 None,
 0.07002482316952552,
 array([0.0824592 , 0.1005652 , 0.00217632, ..., 0.00956451, 0.15155933,
        0.55687694]))

In [167]:
total = list(zip(x, cat_ind.iloc[:,0]))
print(sum([1 for pair in total if round(pair[0]) == pair[1]])/len(total))

0.4894472361809045


In [102]:
weights = list(abs(np.random.normal(loc = 0, scale = 0.01, size = (1,cat_car_df.shape[1])))[0])

In [108]:
zed = get_z_vals(X_scaled, weights, 3)

In [109]:
zed

array([ 0.64235398,  0.80352823, -3.1020312 , ..., -1.10570829,
        1.19058833,  3.19529599])

In [110]:
preds = get_y_hat(zed)

In [111]:
preds

array([0.65528539, 0.6907287 , 0.04302355, ..., 0.24867186, 0.76684627,
       0.96065687])

In [112]:
cost_fun(cat_ind, preds)

3918.576307428814

In [147]:
from sklearn.metrics import log_loss

In [69]:
from sklearn import preprocessing

In [70]:
scaler = preprocessing.StandardScaler().fit(cat_car_df)
X_scaled = scaler.transform(cat_car_df)

In [71]:
X_scaled = pd.DataFrame(X_scaled)